In [1]:
from backtesting import Backtest, Strategy
from backtesting.lib import crossover, SignalStrategy, TrailingStrategy, resample_apply
from backtesting.test import SMA
from backtesting import Backtest

import matplotlib.pyplot as plt
from matplotlib.pyplot import figure
import numpy as np
import pandas as pd 
import math as m
import os, glob

C:\Users\maw\AppData\Roaming\Python\Python37\site-packages\backtesting\_plotting.py:37: UserWarning: Jupyter Notebook detected. Setting Bokeh output to notebook. This may not work in Jupyter clients without JavaScript support (e.g. PyCharm, Spyder IDE). Reset with `bokeh.io.reset_output()`.
  warnings.warn('Jupyter Notebook detected. '


Loading BokehJS ...

In [2]:
import warnings
warnings.filterwarnings("ignore")

In [3]:
pwd = os.getcwd()
datasource_path = os.path.join(pwd, r'../../../Datasets/Junio2020/procesados-regression/')
filenames = glob.glob(datasource_path + "/*.csv")
filenames.sort()
for file in filenames:
    print(filenames.index(file), ' ', os.path.basename(file))

0   R-EURUSD_FULL_1D_144F.csv
1   R-EURUSD_FULL_1D_44F.csv
2   R-EURUSD_FULL_1D_69F.csv
3   R-EURUSD_FULL_1H_44F.csv
4   R-EURUSD_FULL_1H_49F.csv


In [4]:
INDEX =2

dateparse = lambda x: pd.datetime.strptime(x, '%Y-%m-%d %H:%M:%S')
DATASET = pd.read_csv(filenames[INDEX], header=0)
print(DATASET.head(5))
print(DATASET.shape)
print(DATASET.columns)


     Gmt time     Open     High      Low    Close        Volume  Open_Bid  \
0  2004-01-01  1.25950  1.26052  1.24698  1.25733  4.621817e+05   1.25934   
1  2004-01-02  1.25717  1.26282  1.25214  1.25832  1.066578e+06   1.25701   
2  2004-01-04  1.25925  1.26487  1.25789  1.26318  6.879980e+04   1.25855   
3  2004-01-05  1.26324  1.26935  1.26301  1.26830  1.119689e+06   1.26308   
4  2004-01-06  1.26836  1.28093  1.26666  1.27150  1.125442e+06   1.26820   

   High_Bid  Low_Bid  Close_Bid  ...    Trix_2  Trix_5 Trix_15  Trix_25  \
0   1.26035  1.24679    1.25723  ...  0.000000     0.0     0.0      0.0   
1   1.26263  1.25198    1.25806  ...  0.000332     0.0     0.0      0.0   
2   1.26477  1.25779    1.26308  ...  0.001495     0.0     0.0      0.0   
3   1.26924  1.26288    1.26820  ...  0.002496     0.0     0.0      0.0   
4   1.28083  1.26650    1.27140  ...  0.002732     0.0     0.0      0.0   

   Trix_50  Trix_75  MACD_5_25  MACDsign_5_25  MACDdiff_5_25  \
0      0.0      0.0   

In [5]:
INICIO = 0

sub_DATASET = DATASET.iloc[-INICIO:]
print(sub_DATASET.shape)

(5137, 69)


In [6]:
class Position(SignalStrategy):
    def init(self):
        global df
        super().init()  
        self.set_signal(self.data.Position)

In [7]:
class limits(SignalStrategy, TrailingStrategy):
    buy_lim = 0.99
    sell_lim = -0.99
    
    def init(self):
        super().init()
        self.Op_Abierta = False
        
    def next(self):
        sig = self.data.Position[-1]
        if not self.Op_Abierta and sig >= self.buy_lim:
            self.buy()
            self.Op_Abierta = True
        if self.Op_Abierta and sig <= self.sell_lim:
            self.sell()
            self.Op_Abierta = False

In [8]:
class limits2(SignalStrategy, TrailingStrategy):
    buy_lim = 0.99
    sell_lim = -0.99
    
    def init(self):
        super().init()
        
    def next(self):
        sig = self.data.Position[-1]
        if  sig >= self.buy_lim:
            self.buy()
        if  sig <= self.sell_lim:
            self.sell()

In [10]:
dataN = pd.DataFrame()

class optimized(SignalStrategy, TrailingStrategy):
    buy_lim = 0.99
    sell_lim = -0.99
    
    NEG_UNO = -0.001793
    UNO = 0.001931
    NEG_DOS = -0.0035
    DOS = 0.0035
    
    
    def init(self):
        super().init()
        global dataN

        
        self.Op_Abierta = False
        dataN['Pct_Range_Close'] = self.data.Pct_Range_Close
        dataN['Class'] = 0
        
        #dataN.loc[dataN['Pct_Range_Close'] <= self.NEG_UNO, 'Class'] = -1
        #dataN.loc[dataN['Pct_Range_Close'] >= self.UNO, 'Class'] = 1

        dataN.loc[dataN['Pct_Range_Close'] <= self.NEG_DOS, 'Class'] = -1
        dataN.loc[dataN['Pct_Range_Close'] >=  self.DOS, 'Class'] = 1
        
        dataN['Class'] = dataN['Class'].shift(-2)
        dataN['Class'].fillna(0, inplace=True)
        self.i = 0
        
        
    def next(self):
        #print('index ',str(self.i))
        #print(self.data.Close[-1])
        #print(self.data.Pct_Range_Close[-1])
        if not self.Op_Abierta and dataN['Class'][self.i] == 1:
            #print(dataN['Class'][self.i])
            #print('buy')
            self.buy()
            self.Op_Abierta = True
        elif self.Op_Abierta and dataN['Class'][self.i] == -1:
            #print(dataN['Class'][self.i])
            #print('sell')
            self.sell()
            self.Op_Abierta = False
        #else:
        #    print(' No operation')
        
        self.i=self.i+1
#        self.set_signal(pd.Series(self.Position.Class),plot=True)

In [11]:
bt = Backtest(sub_DATASET, optimized, cash=1000, commission=.0001)
bt.run()

Start                               0
End                              5136
Duration                         5136
Exposure [%]                  99.8832
Equity Final [$]          3.73593e+09
Equity Peak [$]           3.73593e+09
Return [%]                3.73593e+08
Buy & Hold Return [%]          11.592
Max. Drawdown [%]            -1.24813
Avg. Drawdown [%]           -0.221236
Max. Drawdown Duration             35
Avg. Drawdown Duration        3.06848
# Trades                         1106
Win Rate [%]                  98.8246
Best Trade [%]                12.9601
Worst Trade [%]             -0.599745
Avg. Trade [%]                1.37143
Max. Trade Duration                37
Avg. Trade Duration           4.63834
Expectancy [%]                1.37605
SQN                           9.92006
Sharpe Ratio                  1.19698
Sortino Ratio                 7.91805
Calmar Ratio                  1.09878
_strategy                   optimized
dtype: object

In [12]:
bt.plot()

In [26]:
START = 0.0035
END = 0.0036
ITERACIONES = 10

In [27]:
UNO_VECTOR = np.linspace(START,END,ITERACIONES)
UNO_VECTOR.tolist()

[0.0035,
 0.003511111111111111,
 0.003522222222222222,
 0.003533333333333333,
 0.0035444444444444442,
 0.0035555555555555557,
 0.0035666666666666668,
 0.003577777777777778,
 0.003588888888888889,
 0.0036]

In [28]:
UNO_NEG_VECTOR = np.linspace(START*-1,END*-1,ITERACIONES)
UNO_NEG_VECTOR.tolist()

[-0.0035,
 -0.003511111111111111,
 -0.003522222222222222,
 -0.003533333333333333,
 -0.0035444444444444442,
 -0.0035555555555555557,
 -0.0035666666666666668,
 -0.003577777777777778,
 -0.003588888888888889,
 -0.0036]

In [29]:
bt.optimize(NEG_UNO = UNO_NEG_VECTOR.tolist(),
                  UNO = UNO_VECTOR.tolist(),
           maximize='Win Rate [%]',
            return_heatmap=True
           )

(Start                                                         0
 End                                                        5136
 Duration                                                   5136
 Exposure [%]                                            99.8832
 Equity Final [$]                                    3.73593e+09
 Equity Peak [$]                                     3.73593e+09
 Return [%]                                          3.73593e+08
 Buy & Hold Return [%]                                    11.592
 Max. Drawdown [%]                                      -1.24813
 Avg. Drawdown [%]                                     -0.221236
 Max. Drawdown Duration                                       35
 Avg. Drawdown Duration                                  3.06848
 # Trades                                                   1106
 Win Rate [%]                                            98.8246
 Best Trade [%]                                          12.9601
 Worst Trade [%]         

In [30]:
bt._results['_strategy']

<Strategy optimized(NEG_UNO=-0.0035,UNO=0.0035)>

In [31]:
bt.plot()